In [1]:
import re
import time
import timeit
import traceback

from tqdm import tqdm
import numpy as np
import pandas as pd
from selenium import webdriver # webdriver 操作一般用
from selenium.webdriver.chrome import service as fs # Chrome を driver として設定する用
from selenium.webdriver.chrome.options import Options # headless モードで作業する用
from selenium.webdriver.common.by import By # find_element() で参照したい位置を特定する用
from bs4 import BeautifulSoup 

In [2]:
# chrome driver の PATH 
DRIVER_PATH = '/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/chromedriver'
service = fs.Service(executable_path=DRIVER_PATH)

options = Options()
options.add_argument("--window-size=1920,1200")
# options.add_argument('--headless')

In [3]:
# 起動
driver = webdriver.Chrome(options=options, service=service)

# 作業したい url を指定し、開く
BASE_URL = 'https://www3.nhk.or.jp/news/easy'
driver.get(BASE_URL)

# get_easy_url: 最新日付分取得

In [4]:
# click して特定日付の記事一覧を表示する
driver.execute_script('window.scrollTo(0, 1000);')
element = driver.find_element(By.XPATH, '//*[@id="easy-wrapper"]/div[2]/aside/section[2]/div[1]/a[1]')
element.click()

# utf-8 に変換する
html = driver.page_source.encode('utf-8')

soup = BeautifulSoup(html, 'html.parser')

easy_urls_raw = soup.select('#js-archives-list > a')
date = soup.select_one('#js-pager-date').text

# 7.67 µs ± 28.2 ns per loop (mean ± std. dev. of 7 runs, 100,000 loops each)
easy_urls = []
dates = []
for url in tqdm(easy_urls_raw):
    new_url = re.sub(r'^./', BASE_URL+'/', url.get('href'))
    easy_urls = np.append(easy_urls, new_url)

dates = np.append(dates, np.repeat(date, len(easy_urls)))


easy_urls, dates

100%|██████████| 4/4 [00:00<00:00, 4841.91it/s]


(array(['https://www3.nhk.or.jp/news/easy/k10013903131000/k10013903131000.html',
        'https://www3.nhk.or.jp/news/easy/k10013901891000/k10013901891000.html',
        'https://www3.nhk.or.jp/news/easy/k10013901431000/k10013901431000.html',
        'https://www3.nhk.or.jp/news/easy/k10013901261000/k10013901261000.html'],
       dtype='<U69'),
 array(['11月25日', '11月25日', '11月25日', '11月25日'], dtype='<U32'))

In [193]:
a = []
len(a)
np.repeat('Unexpected', 4)

array(['Unexpected', 'Unexpected', 'Unexpected', 'Unexpected'],
      dtype='<U10')

# get_easy_url: 過去分取得

In [5]:
# href には 11 月 25 日分が保存されており、11 月 24 日から 365 日分遡るコードを走らせる
for i in tqdm(range(250)): # 0, 1, 2, ... 364 まで
    try:
        # click して特定日付の記事一覧を表示する
        driver.execute_script('window.scrollTo(0, 1000);')
        element = driver.find_element(By.XPATH, '//*[@id="easy-wrapper"]/div[2]/aside/section[2]/div[1]/a[2]')
        element.click()

        # utf-8 に変換する
        html = driver.page_source.encode('utf-8')

        soup = BeautifulSoup(html, 'html.parser')

        article_raw = soup.select('#js-archives-list > a')
        date = soup.select_one('#js-pager-date').text

        easy_urls_raw = []

        try:
            for ref in article_raw:
                new_url = re.sub(r'^./', BASE_URL+'/', ref.get('href'))
                easy_urls_raw = np.append(easy_urls_raw, new_url)
                time.sleep(1)
        
        except:
            print(f'date: {date} \nposition: #{len(easy_urls)}th row \n')
            traceback.print_exc()
            easy_urls = np.append(easy_urls, np.repeat(np.nan, 4-len(easy_urls_raw)))
            dates = np.append(dates, [date]*(4-len(easy_urls_raw)))

        easy_urls = np.append(easy_urls, easy_urls_raw)
        dates = np.append(dates, np.repeat(date, len(easy_urls_raw)))
        
    except:
        date = soup.select_one('#js-pager-date').text
        print(f'date: {date} \nposition: #{len(easy_urls)}th row \n')
        traceback.print_exc()
        easy_urls = np.concatenate([easy_urls, [np.nan]*4])
        dates = np.append(dates, [date]*4)
        
        


easy_urls, dates

 97%|█████████▋| 243/250 [16:35<00:25,  3.60s/it]Traceback (most recent call last):
  File "/var/folders/ng/b98db55j0msdb5ddc0lr6sh40000gn/T/ipykernel_69623/3567192175.py", line 7, in <module>
    element.click()
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webelement.py", line 93, in click
    self._execute(Command.CLICK_ELEMENT)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webelement.py", line 410, in _execute
    return self._parent.execute(command, params)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webdriver.py", line 444, in execute
    self.error_handler.check_response(response)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/errorhandler.py", line 249, in check_response
    raise exception_class(message, screen, stacktrace)
selenium.common.exceptions.ElementClickI

date: 11月25日 
position: #969th row 



Traceback (most recent call last):
  File "/var/folders/ng/b98db55j0msdb5ddc0lr6sh40000gn/T/ipykernel_69623/3567192175.py", line 7, in <module>
    element.click()
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webelement.py", line 93, in click
    self._execute(Command.CLICK_ELEMENT)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webelement.py", line 410, in _execute
    return self._parent.execute(command, params)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webdriver.py", line 444, in execute
    self.error_handler.check_response(response)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/errorhandler.py", line 249, in check_response
    raise exception_class(message, screen, stacktrace)
selenium.common.exceptions.ElementClickInterceptedException: Message: element click inter

date: 11月25日 
position: #973th row 



Traceback (most recent call last):
  File "/var/folders/ng/b98db55j0msdb5ddc0lr6sh40000gn/T/ipykernel_69623/3567192175.py", line 7, in <module>
    element.click()
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webelement.py", line 93, in click
    self._execute(Command.CLICK_ELEMENT)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webelement.py", line 410, in _execute
    return self._parent.execute(command, params)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webdriver.py", line 444, in execute
    self.error_handler.check_response(response)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/errorhandler.py", line 249, in check_response
    raise exception_class(message, screen, stacktrace)
selenium.common.exceptions.ElementClickInterceptedException: Message: element click inter

...

Traceback (most recent call last):
  File "/var/folders/ng/b98db55j0msdb5ddc0lr6sh40000gn/T/ipykernel_69623/3567192175.py", line 7, in <module>
    element.click()
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webelement.py", line 93, in click
    self._execute(Command.CLICK_ELEMENT)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webelement.py", line 410, in _execute
    return self._parent.execute(command, params)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webdriver.py", line 444, in execute
    self.error_handler.check_response(response)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/errorhandler.py", line 249, in check_response
    raise exception_class(message, screen, stacktrace)
selenium.common.exceptions.ElementClickInterceptedException: Message: element click inter

date: 11月25日 
position: #989th row 



Traceback (most recent call last):
  File "/var/folders/ng/b98db55j0msdb5ddc0lr6sh40000gn/T/ipykernel_69623/3567192175.py", line 7, in <module>
    element.click()
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webelement.py", line 93, in click
    self._execute(Command.CLICK_ELEMENT)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webelement.py", line 410, in _execute
    return self._parent.execute(command, params)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webdriver.py", line 444, in execute
    self.error_handler.check_response(response)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/errorhandler.py", line 249, in check_response
    raise exception_class(message, screen, stacktrace)
selenium.common.exceptions.ElementClickInterceptedException: Message: element click inter

date: 11月25日 
position: #993th row 



(array(['https://www3.nhk.or.jp/news/easy/k10013903131000/k10013903131000.html',
        'https://www3.nhk.or.jp/news/easy/k10013901891000/k10013901891000.html',
        'https://www3.nhk.or.jp/news/easy/k10013901431000/k10013901431000.html',
        'https://www3.nhk.or.jp/news/easy/k10013901261000/k10013901261000.html',
        'https://www3.nhk.or.jp/news/easy/k10013901291000/k10013901291000.html',
        'https://www3.nhk.or.jp/news/easy/k10013900291000/k10013900291000.html',
        'https://www3.nhk.or.jp/news/easy/k10013898591000/k10013898591000.html',
        'https://www3.nhk.or.jp/news/easy/k10013898071000/k10013898071000.html',
        'https://www3.nhk.or.jp/news/easy/k10013899241000/k10013899241000.html',
        'https://www3.nhk.or.jp/news/easy/k10013897731000/k10013897731000.html',
        'https://www3.nhk.or.jp/news/easy/k10013897051000/k10013897051000.html',
        'https://www3.nhk.or.jp/news/easy/k10013897461000/k10013897461000.html',
        'https://www3.nhk.or

# easy_extraction

In [6]:
easy_articles = []

for url in tqdm(easy_urls):
    try:
        driver.get(url)

        # HTML を文字コードを UTF-8 に変換してから取得する。
        html = driver.page_source.encode('utf-8')

        # BeautifulSoup で扱えるようにする
        soup = BeautifulSoup(html, 'html.parser')

        for s in soup(['rt']):
            # BeautifulSoup()の関数:decompose() = 文字削除
            s.decompose()

        # id で特定の要素を取り出す
        article_raw = soup.select_one('#js-article-body').text

        article_raw = re.sub('\n', '', article_raw)
        article_raw = re.sub(' ', '', article_raw)
        easy_articles.append(article_raw)

        time.sleep(1)
    
    except:
        traceback.print_exc()
        easy_articles.append(np.nan)

easy_articles

 97%|█████████▋| 969/997 [25:32<00:46,  1.65s/it]Traceback (most recent call last):
  File "/var/folders/ng/b98db55j0msdb5ddc0lr6sh40000gn/T/ipykernel_69623/1362427552.py", line 5, in <module>
    driver.get(url)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webdriver.py", line 455, in get
    self.execute(Command.GET, {"url": url})
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webdriver.py", line 444, in execute
    self.error_handler.check_response(response)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/errorhandler.py", line 249, in check_response
    raise exception_class(message, screen, stacktrace)
selenium.common.exceptions.InvalidArgumentException: Message: invalid argument
  (Session info: chrome=107.0.5304.110)
Stacktrace:
0   chromedriver                        0x000000010c27d2c8 chromedriver + 4752072
1   chromedri

['塩野義製薬の「ゾコーバ」は、新型コロナウイルスの薬です。日本の会社が初めて作った口から飲む薬です。国は今月22日、「ゾコーバ」を使うことを認めました。この薬は、お年寄りや病気がひどくなる心配がある人だけではなくて、12歳以上だったらどんな人でも使うことができます。加藤厚生労働大臣は25日、「100万人に使う薬の準備ができたので、今月28日から病院で使うことができるようになります」と言いました。この薬を使う2900の病院は、都道府県などのウェブサイトで知らせる予定です。塩野義製薬は新型コロナウイルスのワクチンも作っていて、24日に日本で使う申請をしました。',
 'サッカーのワールドカップを開いているFIFAは24日、日本の選手たちが試合の会場で使ったあとのロッカールームの写真をツイッターに出しました。ロッカールームは、タオルなどを畳んで、きれいに片付けてあります。FIFAはツイッターで「日本の選手は、歴史に残る試合をしてドイツに勝ったあと、ロッカールームをこのようにしてから帰りました。本当にきれいです」と褒めました。そして「Domo\u3000Arigato（どうもありがとう）」と書きました。FIFAは、日本のファンが試合のあと会場のごみを掃除したことについても、ウェブサイトなどですばらしいと言っています。',
 '山口大学の小島渉先生は今年8月、山口市の林でカブトムシを調べました。カブトムシは夜から朝に活動します。朝5時ごろ、カブトムシは木に集まって樹液を吸っていました。しかし、あとからオオスズメバチという蜂が来て、カブトムシの足をかみました。蜂はカブトムシを木から落としたあと、樹液を吸いました。小島先生は、蜂が来ないようにする薬をスプレーしてみました。蜂がいなくなると、カブトムシの半分以上は昼まで樹液を吸っていました。小島先生は「夜に活動するのはカブトムシの性質だと思っていました。しかし、昼は蜂がいるから、活動する時間が変わったのかもしれません。新しい考え方を見つけることができました」と話しています。',
 '新しい会社に移ったり、今の会社の中で成長しそうなところに移ったりするために、新しい技術などを習うことを「リスキリング」といいます。政府は、リスキリングで会社の利益や給料などがもっと上がると考えています。これを進める会社にお金を出すことを考えていて、関心

# get_regular_url(Regular)

In [7]:
regular_urls = []

for url in tqdm(easy_urls):
    try:
        # 作業したい url を指定し、開く
        driver.get(url)

        # utf-8 に変換する
        html = driver.page_source.encode('utf-8')

        soup = BeautifulSoup(html, 'html.parser')

        regular_url = soup.select_one('#js-regular-news').get('href')
        regular_urls.append(regular_url)

        time.sleep(1)

    except:
        traceback.print_exc()
        regular_urls.append(np.nan)

regular_urls

 97%|█████████▋| 969/997 [25:27<00:43,  1.57s/it]Traceback (most recent call last):
  File "/var/folders/ng/b98db55j0msdb5ddc0lr6sh40000gn/T/ipykernel_69623/3404145459.py", line 6, in <module>
    driver.get(url)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webdriver.py", line 455, in get
    self.execute(Command.GET, {"url": url})
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/webdriver.py", line 444, in execute
    self.error_handler.check_response(response)
  File "/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/webdriver/remote/errorhandler.py", line 249, in check_response
    raise exception_class(message, screen, stacktrace)
selenium.common.exceptions.InvalidArgumentException: Message: invalid argument
  (Session info: chrome=107.0.5304.110)
Stacktrace:
0   chromedriver                        0x000000010c27d2c8 chromedriver + 4752072
1   chromedri

['https://www3.nhk.or.jp/news/html/20221125/k10013903131000.html',
 'https://www3.nhk.or.jp/news/html/20221124/k10013901891000.html',
 'https://www3.nhk.or.jp/news/html/20221123/k10013901431000.html',
 'https://www3.nhk.or.jp/news/html/20221123/k10013901261000.html',
 'https://www3.nhk.or.jp/news/html/20221123/k10013901291000.html',
 'https://www3.nhk.or.jp/news/html/20221122/k10013900291000.html',
 'https://www3.nhk.or.jp/news/html/20221121/k10013898591000.html',
 'https://www3.nhk.or.jp/news/html/20221121/k10013898071000.html',
 'https://www3.nhk.or.jp/news/html/20221121/k10013899241000.html',
 'https://www3.nhk.or.jp/news/html/20221120/k10013897731000.html',
 'https://www3.nhk.or.jp/news/html/20221119/k10013897051000.html',
 'https://www3.nhk.or.jp/news/html/20221119/k10013897461000.html',
 'https://www3.nhk.or.jp/news/html/20221120/k10013897951000.html',
 'https://www3.nhk.or.jp/news/html/20221120/k10013897921000.html',
 'https://www3.nhk.or.jp/news/html/20221118/k10013895631000.ht

# regular_extraction

In [8]:
regular_articles = []

for url in tqdm(regular_urls):
    try:
        driver.get(url)

        # utf-8 に変換する
        html = driver.page_source.encode('utf-8')

        soup = BeautifulSoup(html, 'html.parser')

        for n in soup(['nav']):
            n.decompose()

        for t in soup(['h2']):
            t.decompose()
        
        try:
            article_raw = soup.select_one('#main > article.module.module--detail--v3 > section > section').text

        except AttributeError:
            article_raw = soup.select_one('#main > article.module.module--detail > section.module--detail-content > section > div').text

        article_raw = re.sub('\n', '', article_raw)
        article_raw = re.sub(' ', '', article_raw)
        regular_articles.append(article_raw)
        
        time.sleep(1)

    except:
        traceback.print_exc()
        regular_articles.append(np.nan)
        print(f'\nposition of error: #{len(regular_articles)}th row \n')
        traceback.print_exc()

        
regular_articles

  6%|▌         | 58/997 [01:32<22:35,  1.44s/it]Traceback (most recent call last):
  File "/var/folders/ng/b98db55j0msdb5ddc0lr6sh40000gn/T/ipykernel_69623/2405481427.py", line 19, in <module>
    article_raw = soup.select_one('#main > article.module.module--detail--v3 > section > section').text
AttributeError: 'NoneType' object has no attribute 'text'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/var/folders/ng/b98db55j0msdb5ddc0lr6sh40000gn/T/ipykernel_69623/2405481427.py", line 22, in <module>
    article_raw = soup.select_one('#main > article.module.module--detail > section.module--detail-content > section > div').text
AttributeError: 'NoneType' object has no attribute 'text'
  8%|▊         | 79/997 [02:06<25:58,  1.70s/it]Traceback (most recent call last):
  File "/var/folders/ng/b98db55j0msdb5ddc0lr6sh40000gn/T/ipykernel_69623/2405481427.py", line 19, in <module>
    article_raw = soup.select_one('#main > article

['塩野義製薬が開発し国に承認された新型コロナの飲み薬「ゾコーバ」は、当初の予定を前倒しし、週明け28日から医療機関への本格的な供給が始まる見通しになりました。国内の製薬会社として初めて塩野義製薬が開発した新型コロナの飲み薬「ゾコーバ」は、今月22日に国が使用を承認し、重症化リスクの低い患者も軽症段階から服用できるのが特長です。加藤厚生労働大臣は、閣議のあと記者団に対し「契約を締結していた100万人分がすでに納入され、流通システムの準備作業も円滑に進んだ。12月初頭からとお伝えしていたが、週明け28日から本格的な供給を開始することになった」と述べました。供給されるのは全国のおよそ2900の医療機関などで、都道府県などのホームページで公開される予定です。すでに発注があった一部の医療機関には、早ければ25日にも発送されるということです。また、加藤大臣は「ゾコーバ」が新たな「緊急承認制度」で承認されたことをめぐり、専門家から「迅速な承認」と「有効性や安全性の確認」の両立が課題だという指摘が出ていることを踏まえ、「課題を整理し、今後の緊急承認をどう捉えていけばいいのか議論したい」と述べました。',
 'FIFA＝国際サッカー連盟は公式ツイッターで、ドイツ戦で勝利した日本代表のロッカールームの写真を紹介し、「汚れ一つない」として感謝のことばを書き込んでいます。FIFAの公式ツイッターは24日、日本代表がワールドカップ1次リーグの初戦で強豪のドイツに逆転で勝利し、引き上げたあとのロッカールームの写真を投稿しました。ロッカールームは整理整頓され、タオルなどもきれいに畳まれていて、「歴史的な勝利のあとです。日本のファンがスタジアムのごみを掃除してくれた一方で、日本代表もロッカールームをこのような状態にして引き上げていきました。汚れ一つありません」と褒めたたえ、「DomoArigato（どうもありがとう）」と、日本語のつづりで感謝のことばを書き込んでいます。また机の上には折り鶴とともに、日本語とアラビア語で「ありがとう」と書き置きされた写真を掲載し、「これも彼らが残していってくれました」と投稿されています。今大会、試合後に会場のごみを掃除する日本のファンの姿も話題になっていて、FIFAは公式ホームページなどで「模範を示している」と紹介しています。',
 '夏の雑木林で夜間や早朝に活動

# 結合

In [9]:
len(easy_urls), len(easy_articles), len(regular_urls), len(regular_articles), len(dates)

(997, 997, 997, 997, 997)

In [10]:
easy_urls_REAL = easy_urls.copy()
easy_urls_REAL

array(['https://www3.nhk.or.jp/news/easy/k10013903131000/k10013903131000.html',
       'https://www3.nhk.or.jp/news/easy/k10013901891000/k10013901891000.html',
       'https://www3.nhk.or.jp/news/easy/k10013901431000/k10013901431000.html',
       'https://www3.nhk.or.jp/news/easy/k10013901261000/k10013901261000.html',
       'https://www3.nhk.or.jp/news/easy/k10013901291000/k10013901291000.html',
       'https://www3.nhk.or.jp/news/easy/k10013900291000/k10013900291000.html',
       'https://www3.nhk.or.jp/news/easy/k10013898591000/k10013898591000.html',
       'https://www3.nhk.or.jp/news/easy/k10013898071000/k10013898071000.html',
       'https://www3.nhk.or.jp/news/easy/k10013899241000/k10013899241000.html',
       'https://www3.nhk.or.jp/news/easy/k10013897731000/k10013897731000.html',
       'https://www3.nhk.or.jp/news/easy/k10013897051000/k10013897051000.html',
       'https://www3.nhk.or.jp/news/easy/k10013897461000/k10013897461000.html',
       'https://www3.nhk.or.jp/news/easy

In [11]:
data = pd.DataFrame({
    'Date': dates,
    'easy URL': easy_urls,
    'easy article': easy_articles,
    'regular URL': regular_urls,
    'regular articles': regular_articles
})
display(data)
data.isna().sum()

Date                                           easy URL  \
0    11月25日  https://www3.nhk.or.jp/news/easy/k100139031310...   
1    11月25日  https://www3.nhk.or.jp/news/easy/k100139018910...   
2    11月25日  https://www3.nhk.or.jp/news/easy/k100139014310...   
3    11月25日  https://www3.nhk.or.jp/news/easy/k100139012610...   
4    11月24日  https://www3.nhk.or.jp/news/easy/k100139012910...   
..      ...                                                ...   
992  11月25日                                                nan   
993  11月25日                                                nan   
994  11月25日                                                nan   
995  11月25日                                                nan   
996  11月25日                                                nan   

                                          easy article  \
0    塩野義製薬の「ゾコーバ」は、新型コロナウイルスの薬です。日本の会社が初めて作った口から飲む薬...   
1    サッカーのワールドカップを開いているFIFAは24日、日本の選手たちが試合の会場で使ったあと...   
2    山口大学の小島渉先生は今年8月、山口市の林でカブトムシを調べました。カブトムシは夜から朝に活...   
3    新しい会社に移ったり、今の会社の中で成長しそうなところに移ったりするために、新しい技術などを...   
4    カタールで行っているサッカーのワールドカップで23日、日本とドイツの試合がありました。ドイツ...   
..                                                 ...   
992                                                NaN   
993                                                NaN   
994                                                NaN   
995                                                NaN   
996                                                NaN   

                                           regular URL  \
0    https://www3.nhk.or.jp/news/html/20221125/k100...   
1    https://www3.nhk.or.jp/news/html/20221124/k100...   
2    https://www3.nhk.or.jp/news/html/20221123/k100...   
3    https://www3.nhk.or.jp/news/html/20221123/k100...   
4    https://www3.nhk.or.jp/news/html/20221123/k100...   
..                                                 ...   
992                                                NaN   
993                                                NaN   
994                                                NaN   
995                                                NaN   
996                                                NaN   

                                      regular articles  
0    塩野義製薬が開発し国に承認された新型コロナの飲み薬「ゾコーバ」は、当初の予定を前倒しし、週明...  
1    FIFA＝国際サッカー連盟は公式ツイッターで、ドイツ戦で勝利した日本代表のロッカールームの写...  
2    夏の雑木林で夜間や早朝に活動するカブトムシ。もともと夜行性と考えられてきましたが、実はある強...  
3    新たな職業に就いたり、成長が見込める社内の別の部署に移ったりするために必要なスキルを身につけ...  
4    サッカーのワールドカップカタール大会、世界ランキング24位でグループEの日本は23日の1次リ...  
..                                                 ...  
992                                                NaN  
993                                                NaN  
994                                                NaN  
995                                                NaN  
996                                                NaN  

[997 rows x 5 columns]

Date                 0
easy URL             0
easy article        28
regular URL         28
regular articles    40
dtype: int64

In [12]:
data = data[:969]
display(data.isna())
data.isna().sum()

Date  easy URL  easy article  regular URL  regular articles
0    False     False         False        False             False
1    False     False         False        False             False
2    False     False         False        False             False
3    False     False         False        False             False
4    False     False         False        False             False
..     ...       ...           ...          ...               ...
964  False     False         False        False             False
965  False     False         False        False              True
966  False     False         False        False             False
967  False     False         False        False              True
968  False     False         False        False              True

[969 rows x 5 columns]

Date                 0
easy URL             0
easy article         0
regular URL          0
regular articles    12
dtype: int64

In [13]:
data.to_csv('./data/data_pool.csv')

# nan をどうしようか

In [80]:
for i, url in enumerate(data.loc[data['regular articles'].isnull(), 'regular URL'].reset_index(drop=True)):
    print(
            data.loc[data['regular articles'].isnull(), 'regular URL']\
            .copy()\
            .reset_index(drop=True)\
            [i]
    )

https://www3.nhk.or.jp/news/html/20221031/k10013875551000.html
https://www3.nhk.or.jp/news/html/20221021/k10013865621000.html
https://www3.nhk.or.jp/news/html/20220909/k10013809381000.html
https://www3.nhk.or.jp/news/html/20220907/k10013807191000.html
https://www3.nhk.or.jp/news/html/20220404/k10013566171000.html
https://www3.nhk.or.jp/news/html/20220101/k10013411541000.html
https://www3.nhk.or.jp/news/html/20211127/k10013364701000.html
https://www3.nhk.or.jp/news/html/20211126/k10013362101000.html
https://www3.nhk.or.jp/news/html/20211125/k10013361621000.html
https://www3.nhk.or.jp/news/html/20211124/k10013359611000.html
https://www3.nhk.or.jp/news/html/20211124/k10013359771000.html
https://www3.nhk.or.jp/news/html/20211124/k10013359681000.html


In [161]:
# chrome driver の PATH 
DRIVER_PATH = '/Users/domolm/.pyenv/versions/3.10.8/lib/python3.10/site-packages/selenium/chromedriver'
service = fs.Service(executable_path=DRIVER_PATH)

options = Options()
options.add_argument("--window-size=1920,1200")

# 作業したい url を指定し、開く
na_urls = data.loc[data['regular articles'].isnull(), 'regular URL']\
        .reset_index(drop=True)
na_articles = []

for url in na_urls:
        try:# 起動
                driver = webdriver.Chrome(options=options, service=service)
                driver.get(url)

                time.sleep(1)

                # utf-8 に変換する
                html = driver.page_source.encode('utf-8')

                soup = BeautifulSoup(html, 'html.parser')

                for t in soup(['h2']):
                        t.decompose()
                for f in soup(['figcaption']):
                        f.decompose()
                for w in soup.findAll(class_='content--editor-body'):
                        w.decompose()

                article_raw = soup.find(class_='content--detail-body')

                article_raw = article_raw.text

                article = re.sub(" ", "", article_raw)

                na_articles.append(article)
        except:
                if re.search('記事が見つかりません', soup.text) != None:
                        na_articles.append('Not Found')
                else:
                        na_articles.append('Unexpected')
        
        else:
                na_articles.append('Unexpected')
        
        finally:
                driver.quit()


In [162]:
na_articles

['Not Found',
 'Not Found',
 'Not Found',
 'Not Found',
 'Not Found',
 'Not Found',
 'Not Found',
 'Not Found']

In [163]:
data.loc[data['regular articles'].isnull(), 'regular articles'] = na_articles

In [168]:
data.isna().sum()

Unnamed: 0.1        0
Unnamed: 0          0
Date                0
easy URL            0
easy article        0
regular URL         0
regular articles    0
dtype: int64

In [165]:
data['regular articles'].value_counts()

Not Found                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               

In [166]:
data.to_csv('./data/data_pool.csv', index=False)

# data check 用

In [152]:
data[58*4-1:58*4+4+1]

Unnamed: 0        Date  \
231         231  2022-08-31   
232         232  2022-08-30   
233         233  2022-08-30   
234         234  2022-08-30   
235         235  2022-08-30   
236         236  2022-08-29   

                                              easy URL  \
231  https://www3.nhk.or.jp/news/easy/k100137932310...   
232  https://www3.nhk.or.jp/news/easy/k100137938810...   
233  https://www3.nhk.or.jp/news/easy/k100137925010...   
234  https://www3.nhk.or.jp/news/easy/k100137910310...   
235  https://www3.nhk.or.jp/news/easy/k100137912910...   
236  https://www3.nhk.or.jp/news/easy/k100137908810...   

                                          easy article  \
231  国は今まで、日本で勉強する外国人の留学生を1年で30万人にすると言っていました。岸田総理大臣...   
232  2011年3月、福島県にある原子力発電所で事故がありました。事故のあと、国は放射線の量が多い...   
233  「霊感商法」は、人に心配なことを言って、とても高い物を買わせることです。消費者庁は29日、霊...   
234  文部科学省の研究所は、物理学など科学の22の分野の世界の論文を調べました。論文が引用されるこ...   
235  東京都は、新型コロナウイルスがうつったあとの後遺症について調べました。オミクロン株が広がった...   
236  アメリカのニューヨークにある国連で、核兵器を減らすためのNPTという条約について話し合う会議...   

                                           regular URL  \
231  https://www3.nhk.or.jp/news/html/20220829/k100...   
232  https://www3.nhk.or.jp/news/html/20220830/k100...   
233  https://www3.nhk.or.jp/news/html/20220829/k100...   
234  https://www3.nhk.or.jp/news/html/20220828/k100...   
235  https://www3.nhk.or.jp/news/html/20220828/k100...   
236  https://www3.nhk.or.jp/news/html/20220827/k100...   

                                      regular articles  
231  岸田総理大臣は永岡文部科学大臣に対し、年間30万人の外国人留学生の受け入れを目指す政府の目標...  
232  東京電力福島第一原子力発電所が立地し、すべての住民の避難が続いてきた福島県双葉町で、30日午...  
233  旧統一教会などの問題を巡って、霊感商法への対応の強化を求める社会的な要請が高まっているとして...  
234  自然科学の分野で、おととしまでの3年間に発表され引用が多かった論文の数を各国で比較したところ...  
235  新型コロナウイルスのオミクロン株の流行が広がったことし、後遺症を訴えて医療機関を受診した人を...  
236  世界の核軍縮の方向性を4週間にわたって協議してきたNPT＝核拡散防止条約の再検討会議は、最終...

In [169]:
data

Unnamed: 0.1  Unnamed: 0        Date  \
0               0           0  2022-11-25   
1               1           1  2022-11-25   
2               2           2  2022-11-25   
3               3           3  2022-11-25   
4               4           4  2022-11-24   
..            ...         ...         ...   
964           964         964  2021-11-26   
965           965         965  2021-11-26   
966           966         966  2021-11-26   
967           967         967  2021-11-25   
968           968         968  2021-11-25   

                                              easy URL  \
0    https://www3.nhk.or.jp/news/easy/k100139031310...   
1    https://www3.nhk.or.jp/news/easy/k100139018910...   
2    https://www3.nhk.or.jp/news/easy/k100139014310...   
3    https://www3.nhk.or.jp/news/easy/k100139012610...   
4    https://www3.nhk.or.jp/news/easy/k100139012910...   
..                                                 ...   
964  https://www3.nhk.or.jp/news/easy/k100133620810...   
965  https://www3.nhk.or.jp/news/easy/k100133596110...   
966  https://www3.nhk.or.jp/news/easy/k100133604110...   
967  https://www3.nhk.or.jp/news/easy/k100133597710...   
968  https://www3.nhk.or.jp/news/easy/k100133596810...   

                                          easy article  \
0    塩野義製薬の「ゾコーバ」は、新型コロナウイルスの薬です。日本の会社が初めて作った口から飲む薬...   
1    サッカーのワールドカップを開いているFIFAは24日、日本の選手たちが試合の会場で使ったあと...   
2    山口大学の小島渉先生は今年8月、山口市の林でカブトムシを調べました。カブトムシは夜から朝に活...   
3    新しい会社に移ったり、今の会社の中で成長しそうなところに移ったりするために、新しい技術などを...   
4    カタールで行っているサッカーのワールドカップで23日、日本とドイツの試合がありました。ドイツ...   
..                                                 ...   
964  今月8日から留学生などの外国人が日本に入ることができるようになりました。しかし、1日に入る人...   
965  毎年冬に、札幌市では凍った道の滑りやすさを知らせる「つるつる予報」が出ます。この予報は、天気...   
966  お年寄りや障害がある人が生活している施設では、新型コロナウイルスがうつらないように、家族など...   
967  1986年11月21日、東京の伊豆大島で大きな噴火がありました。溶岩が家の近くまで来て、住ん...   
968  今年8月、小笠原諸島の海の中で火山が噴火しました。噴火で出た軽石が、沖縄県や東京都の伊豆諸島...   

                                           regular URL  \
0    https://www3.nhk.or.jp/news/html/20221125/k100...   
1    https://www3.nhk.or.jp/news/html/20221124/k100...   
2    https://www3.nhk.or.jp/news/html/20221123/k100...   
3    https://www3.nhk.or.jp/news/html/20221123/k100...   
4    https://www3.nhk.or.jp/news/html/20221123/k100...   
..                                                 ...   
964  https://www3.nhk.or.jp/news/html/20211125/k100...   
965  https://www3.nhk.or.jp/news/html/20211124/k100...   
966  https://www3.nhk.or.jp/news/html/20211125/k100...   
967  https://www3.nhk.or.jp/news/html/20211124/k100...   
968  https://www3.nhk.or.jp/news/html/20211124/k100...   

                                      regular articles  
0    塩野義製薬が開発し国に承認された新型コロナの飲み薬「ゾコーバ」は、当初の予定を前倒しし、週明...  
1    FIFA＝国際サッカー連盟は公式ツイッターで、ドイツ戦で勝利した日本代表のロッカールームの写...  
2    夏の雑木林で夜間や早朝に活動するカブトムシ。もともと夜行性と考えられてきましたが、実はある強...  
3    新たな職業に就いたり、成長が見込める社内の別の部署に移ったりするために必要なスキルを身につけ...  
4    サッカーのワールドカップカタール大会、世界ランキング24位でグループEの日本は23日の1次リ...  
..                                                 ...  
964  新型コロナウイルスの水際対策が緩和された一方で、いまだに、多くの留学生が入国できない状況が続...  
965                                          Not Found  
966  厚生労働省は、全国の高齢者施設などに対し、面会を希望する家族がワクチン接種を済ませている場合...  
967                                          Not Found  
968                                          Not Found  

[969 rows x 7 columns]

In [207]:
data_renamed = data.rename(columns={
    'easy URL': 'Easy URL',
    'easy article': 'Easy article',
    'regular URL': 'Regular article',
    'regular article': 'Regular article'
})
data_renamed.to_csv('./data/data_pool.csv', index=False)

In [221]:
dtdate = pd.to_datetime(data_renamed['Date'])


2022

In [222]:
%%timeit
dtdate.dt.year[0]

236 µs ± 38.5 µs per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


In [227]:
%%timeit
datetime.datetime.strptime(data_renamed.Date[0], '%Y-%m-%d').year

The slowest run took 4.13 times longer than the fastest. This could mean that an intermediate result is being cached.
38.5 µs ± 24.3 µs per loop (mean ± std. dev. of 7 runs, 10,000 loops each)


In [224]:
if datetime.datetime.strptime(data_renamed.Date[0], '%Y-%m-%d').year == 2022:
    print('yes')

yes


# date を datetime 型に

In [55]:
data['Date'] \
  = pd.concat([
        pd.to_datetime(('2022年' + data.Date[:880]), format='%Y年%m月%d日'),
        pd.to_datetime(('2021年' + data.Date[880:]), format='%Y年%m月%d日')
    ])
data['Date']

0     2022-11-25
1     2022-11-25
2     2022-11-25
3     2022-11-25
4     2022-11-24
         ...    
964   2021-11-26
965   2021-11-26
966   2021-11-26
967   2021-11-25
968   2021-11-25
Name: Date, Length: 969, dtype: datetime64[ns]

In [180]:
data

Date                                           easy URL  \
0    2022-11-25  https://www3.nhk.or.jp/news/easy/k100139031310...   
1    2022-11-25  https://www3.nhk.or.jp/news/easy/k100139018910...   
2    2022-11-25  https://www3.nhk.or.jp/news/easy/k100139014310...   
3    2022-11-25  https://www3.nhk.or.jp/news/easy/k100139012610...   
4    2022-11-24  https://www3.nhk.or.jp/news/easy/k100139012910...   
..          ...                                                ...   
964  2021-11-26  https://www3.nhk.or.jp/news/easy/k100133620810...   
965  2021-11-26  https://www3.nhk.or.jp/news/easy/k100133596110...   
966  2021-11-26  https://www3.nhk.or.jp/news/easy/k100133604110...   
967  2021-11-25  https://www3.nhk.or.jp/news/easy/k100133597710...   
968  2021-11-25  https://www3.nhk.or.jp/news/easy/k100133596810...   

                                          easy article  \
0    塩野義製薬の「ゾコーバ」は、新型コロナウイルスの薬です。日本の会社が初めて作った口から飲む薬...   
1    サッカーのワールドカップを開いているFIFAは24日、日本の選手たちが試合の会場で使ったあと...   
2    山口大学の小島渉先生は今年8月、山口市の林でカブトムシを調べました。カブトムシは夜から朝に活...   
3    新しい会社に移ったり、今の会社の中で成長しそうなところに移ったりするために、新しい技術などを...   
4    カタールで行っているサッカーのワールドカップで23日、日本とドイツの試合がありました。ドイツ...   
..                                                 ...   
964  今月8日から留学生などの外国人が日本に入ることができるようになりました。しかし、1日に入る人...   
965  毎年冬に、札幌市では凍った道の滑りやすさを知らせる「つるつる予報」が出ます。この予報は、天気...   
966  お年寄りや障害がある人が生活している施設では、新型コロナウイルスがうつらないように、家族など...   
967  1986年11月21日、東京の伊豆大島で大きな噴火がありました。溶岩が家の近くまで来て、住ん...   
968  今年8月、小笠原諸島の海の中で火山が噴火しました。噴火で出た軽石が、沖縄県や東京都の伊豆諸島...   

                                           regular URL  \
0    https://www3.nhk.or.jp/news/html/20221125/k100...   
1    https://www3.nhk.or.jp/news/html/20221124/k100...   
2    https://www3.nhk.or.jp/news/html/20221123/k100...   
3    https://www3.nhk.or.jp/news/html/20221123/k100...   
4    https://www3.nhk.or.jp/news/html/20221123/k100...   
..                                                 ...   
964  https://www3.nhk.or.jp/news/html/20211125/k100...   
965  https://www3.nhk.or.jp/news/html/20211124/k100...   
966  https://www3.nhk.or.jp/news/html/20211125/k100...   
967  https://www3.nhk.or.jp/news/html/20211124/k100...   
968  https://www3.nhk.or.jp/news/html/20211124/k100...   

                                      regular articles  
0    塩野義製薬が開発し国に承認された新型コロナの飲み薬「ゾコーバ」は、当初の予定を前倒しし、週明...  
1    FIFA＝国際サッカー連盟は公式ツイッターで、ドイツ戦で勝利した日本代表のロッカールームの写...  
2    夏の雑木林で夜間や早朝に活動するカブトムシ。もともと夜行性と考えられてきましたが、実はある強...  
3    新たな職業に就いたり、成長が見込める社内の別の部署に移ったりするために必要なスキルを身につけ...  
4    サッカーのワールドカップカタール大会、世界ランキング24位でグループEの日本は23日の1次リ...  
..                                                 ...  
964  新型コロナウイルスの水際対策が緩和された一方で、いまだに、多くの留学生が入国できない状況が続...  
965                                          Not Found  
966  厚生労働省は、全国の高齢者施設などに対し、面会を希望する家族がワクチン接種を済ませている場合...  
967                                          Not Found  
968                                          Not Found  

[969 rows x 5 columns]

In [179]:
data.to_csv('./data/data_pool.csv', index=False)

In [171]:
import datetime
datetime.datetime(2022, 12, 31) + datetime.timedelta(1)

datetime.datetime(2023, 1, 1, 0, 0)